In [1]:
import geopandas as gpd
import pyproj
import folium
import random
from shapely.geometry import Polygon, MultiPolygon

    Read the contents of a .prj file and return it as a string.

    Args:
        file_path (str): The path to the .prj file.

    Returns:
        str: The contents of the .prj file as a string, or None if the file cannot be read.

In [2]:
def read_prj_file(file_path):
    try:
        with open(file_path, 'r') as prj_file:
            prj_content = prj_file.read()
            return prj_content
    except Exception as e:
        print(f"Error: {e}")
        return None

In [3]:
def transform_coordinates(geometry, proj):
    if isinstance(geometry, Polygon):
        projected_coords = []
        for coords in geometry.exterior.coords:
            projected_coords.append(proj(coords[0], coords[1], inverse=True))
        return Polygon(projected_coords)
    elif isinstance(geometry, MultiPolygon):
        transformed_polygons = []
        for polygon in geometry:
            projected_coords = []
            for coords in polygon.exterior.coords:
                projected_coords.append(proj(coords[0], coords[1], inverse=True))
            transformed_polygons.append(Polygon(projected_coords))
        return MultiPolygon(transformed_polygons)
    else:
        raise ValueError("Unsupported geometry type")

In [4]:
def drop_multipolygons(gdf):
    # Use apply() to filter out rows with MultiPolygons
    gdf = gdf[gdf['geometry'].apply(lambda geom: geom.geom_type == 'Polygon')]
    return gdf

    Keep rows in the GeoDataFrame with a specific year and drop all other years.
    
    Args:
        gdf (geopandas.GeoDataFrame): Input GeoDataFrame.
        specific_year (int): The specific year to keep.
        
    Returns:
        geopandas.GeoDataFrame: GeoDataFrame with rows only for the specific year.
    
    # Filter the GeoDataFrame to keep only rows with the specific year

In [5]:
def keep_specific_year(gdf, specific_years):

    # Print unique years in the 'Year' column
    print("Unique Years in the 'Year' Column:", gdf['Year'].unique())

    filtered_rows = []

    # Iterate over rows of the GeoDataFrame
    for index, fire in gdf.iterrows():
        strYear = fire['Year']
        print(strYear)
        if int(strYear) in specific_years:
            filtered_rows.append(fire)
            print(fire)
    
    # Convert the list of filtered rows back to a GeoDataFrame
    filtered_gdf = gpd.GeoDataFrame(filtered_rows, crs=gdf.crs, geometry='geometry')
    
    return filtered_gdf

In [6]:
# Location of the example shape file and project files
shapefile_path = 'ExampleFiles\\2022_2015_allfires.shp'
prjfile_path = 'ExampleFiles\\2022_2015_allfires.prj'

# Read the shapefile into a GeoDataFrame
gdf = gpd.read_file(shapefile_path)

# Call the drop_multipolygons function to remove MultiPolygons
gdf = drop_multipolygons(gdf)

# Call the drop_years function to remove MultiPolygons
gdf = keep_specific_year(gdf, [2018, 2020, 2022])
#print(filtered_gdf)

Unique Years in the 'Year' Column: ['2018' '2017' '2016' '2015' '2019' '2020' '2021' '0' '2022' '2012' '2011'
 '2013' '2014']
2018
Id                                                         0.0
PhotoID                                     2018_Mar_24_Tinian
FireDate                                                  None
Area                                                    443768
Comments                                                   WV2
FireMonth                                                March
Year                                                      2018
Island                                                  Tinian
Acerage                                             109.657292
geometry     POLYGON ((994879.8793614599 1668873.2891331066...
Name: 0, dtype: object
2018
Id                                                         0.0
PhotoID                                     2018_Mar_24_Tinian
FireDate                                                  None
Area                  

In [7]:
# Convert 'Year' column to integer type if it's not already
gdf['Year'] = gdf['Year'].astype(int)

# Define a color dictionary for each unique year
unique_years = gdf['Year'].unique()
year_colors = {year: "#{:02x}{:02x}{:02x}".format(random.randint(0, 255), random.randint(0, 255), random.randint(0, 255)) for year in unique_years}


In [8]:
# Define the original projection using the provided WKT format
original_proj_wkt = read_prj_file(prjfile_path)

# Create a Proj object from the provided WKT projection information
original_proj = pyproj.Proj(original_proj_wkt)

# Apply coordinate transformation to the 'geometry' column
gdf['geometry'] = gdf['geometry'].apply(lambda geom: transform_coordinates(geom, original_proj))

In [9]:
# Calculate centroid of the first polygon
first_polygon_centroid = gdf['geometry'].iloc[0].centroid
centroid_utm_x, centroid_utm_y = first_polygon_centroid.x, first_polygon_centroid.y
centroid_lat, centroid_lon = original_proj(centroid_utm_x, centroid_utm_y, inverse=True)

# Convert GeoDataFrame to GeoJSON
geojson_data = gdf.to_json()
print(geojson_data)

{"type": "FeatureCollection", "features": [{"id": "0", "type": "Feature", "properties": {"Id": 0.0, "PhotoID": "2018_Mar_24_Tinian", "FireDate": null, "Area": "443768", "Comments": "WV2", "FireMonth": "March", "Year": 2018, "Island": "Tinian", "Acerage": 109.65729164000001}, "geometry": {"type": "Polygon", "coordinates": [[[145.59994720962305, 15.0486539874908], [145.59984209617832, 15.048635833267884], [145.59984502622962, 15.04866952409216], [145.59990775522726, 15.048711236590925], [145.6000049737304, 15.048777651029539], [145.6000334131738, 15.048764051177905], [145.60004086829747, 15.048828381501496], [145.6000138838906, 15.048860357283464], [145.5999945444753, 15.048927583539834], [145.60002564418278, 15.048988998506427], [145.59998924988466, 15.049014793938866], [145.59998878015335, 15.049086728291984], [145.59996615083028, 15.049175362371399], [145.59993605639318, 15.049201196641157], [145.59983690292313, 15.04918987109691], [145.59979150852752, 15.04914673490177], [145.5997450

In [10]:
# Create a map centered over the first polygon
m = folium.Map(location=[centroid_lon, centroid_lat], zoom_start=10)

# Add GeoJSON data to the map with fill color based on 'Year' column
folium.GeoJson(
    geojson_data,
    style_function=lambda feature: {
        'fillColor': year_colors[feature['properties']['Year']],
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.6
    }
).add_to(m)

In [11]:
'''
# Get the centroid coordinates of each polygon and add them as markers
for idx, row in gdf.iterrows():
    centroid = row['geometry'].centroid
    centroid_utm_x, centroid_utm_y = centroid.x, centroid.y
    centroid_lat, centroid_lon = original_proj(centroid_utm_x, centroid_utm_y, inverse=True)
    folium.Marker([centroid_lon, centroid_lat], popup=f'Polygon {idx + 1}').add_to(m)
'''

# Print the map projection type
print("Map Projection Type:", gdf.crs)

m

Map Projection Type: EPSG:32654
